In [25]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.metrics import balanced_accuracy_score
import matplotlib.pyplot as plt
import json

In [76]:
#matchStats_df= pd.read_csv('../datafilev2/datafile/season17-18/season_match_stats.csv')
#seasonStats_df = pd.read_csv('../datafilev2/datafile/season17-18/season_stats.csv')
with open('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8') as f:
    #data = ''.join(f.readlines())
    #data_dict = json.loads(data)
    d = json.load(f)
    
#szn_1718 = pd.read_json('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8')

#season_1718 = json.load(open('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8'))


In [70]:
#data_dict

{'1190418': {'166': {'team_details': {'team_id': '166',
    'team_name': 'Huddersfield',
    'team_rating': '6.14',
    'date': '30/01/2018'},
   'aggregate_stats': {'won_corners': '1',
    'att_sv_low_centre': '1',
    'won_contest': '5',
    'total_tackle': '11',
    'aerial_lost': '15',
    'possession_percentage': '25.3',
    'accurate_pass': '214',
    'total_pass': '308',
    'total_throws': '15',
    'shot_off_target': '2',
    'total_offside': '3',
    'blocked_scoring_att': '2',
    'ontarget_scoring_att': '1',
    'aerial_won': '16',
    'att_miss_left': '1',
    'total_scoring_att': '5',
    'fk_foul_lost': '8',
    'att_miss_right': '1'},
   'Player_stats': {'Jonas Lössl': {'player_details': {'player_id': '131171',
      'player_name': 'Jonas Lössl',
      'player_position_value': '1',
      'player_position_info': 'GK',
      'player_rating': '6.61'},
     'Match_stats': {'good_high_claim': '2',
      'touches': '39',
      'saves': '4',
      'total_pass': '28',
      'fo

In [79]:
#I am going to try code I found in the same page that the dataset was available.
# It shows how this one guy read this dataset into a dataframe, further testing is required (4/21 9:43pm).... 

# create a dictionary containing lists
team_table = {'match_id':[]} ## I (well, actually jordan) sort of did this up above with data_dict

# read through original data
for match_id, match_content in d.items():
    for match_stats in match_content.values():
        team_table['match_id'].append(match_id)
        
        for team_details_label,team_details in match_stats['team_details'].items():
            if team_details_label not in team_table.keys():
                team_table[team_details_label] = []
            team_table[team_details_label].append(team_details)
        
        for team_stats_label,team_stats in match_stats['aggregate_stats'].items():
            if team_stats_label not in team_table.keys():
                team_table[team_stats_label] = []

In [82]:
#right here im just testing shit from above, making sure we getting data correctly listed
match_stats['aggregate_stats'] 

{'att_goal_low_right': '1',
 'won_contest': '10',
 'possession_percentage': '77.1',
 'total_throws': '20',
 'blocked_scoring_att': '3',
 'total_scoring_att': '17',
 'total_tackle': '16',
 'att_miss_high_right': '1',
 'aerial_won': '16',
 'att_miss_right': '3',
 'att_sv_low_centre': '1',
 'aerial_lost': '13',
 'accurate_pass': '762',
 'total_pass': '847',
 'won_corners': '10',
 'shot_off_target': '8',
 'ontarget_scoring_att': '6',
 'goals': '2',
 'att_sv_high_right': '1',
 'att_miss_left': '3',
 'fk_foul_lost': '8',
 'att_goal_low_left': '1',
 'total_offside': '4',
 'att_miss_high': '1',
 'att_sv_low_right': '2'}

In [86]:
#this, again, is from the source mentioned above....

# so far I've created a dictionary containing all the match&team information,
# but no statistic is filled in due to that not all teams have all the data in every matches,
# now I have to deal with missing data:
# filling all statistics with np.nan
for k,v in team_table.items():
    if len(v) == 0:
        team_table[k] = [np.nan] * len(team_table['match_id'])

# indexing by match ID and team ID, if they both matches, fill in the real data
for pos in range(len(team_table['match_id'])):
    for match_id,match_content in d.items():
        for team_id, match_stats in match_content.items():
            for team_stats_label,team_stats in match_stats['aggregate_stats'].items():
                if (team_table['match_id'][pos] == match_id) & (team_table['team_id'][pos] == team_id):
                    team_table[team_stats_label][pos] = team_stats

df = pd.DataFrame(team_table)
df
team_match_data = df.to_csv()
#df.to_csv('team_match_data1718.csv')

match_id team_id          team_name       team_rating        date  \
0    1190418     166       Huddersfield              6.14  30/01/2018   
1    1190418      26          Liverpool  7.22285714285714  30/01/2018   
2    1190424     211           Brighton  7.15384615384615  01/01/2018   
3    1190424     183        Bournemouth  6.90285714285714  01/01/2018   
4    1190342      15            Chelsea  6.77142857142857  13/01/2018   
..       ...     ...                ...               ...         ...   
755  1190373      27            Watford  6.17071428571429  11/03/2018   
756  1190367      32  Manchester United  7.31928571428571  03/02/2018   
757  1190367     166       Huddersfield  6.40857142857143  03/02/2018   
758  1190401      96              Stoke  6.31076923076923  12/03/2018   
759  1190401     167    Manchester City  7.23769230769231  12/03/2018   

    won_corners att_sv_low_centre won_contest total_tackle aerial_lost  ...  \
0             1                 1           5           11          15  ...   
1             4                 2           6           13          16  ...   
2             5                 1          12           23          16  ...   
3            12                 3          17            6          25  ...   
4             6                 1          15           13          18  ...   
..          ...               ...         ...          ...         ...  ...   
755           9                 1           7           13          22  ...   
756           5                 3          27           15          18  ...   
757           2               NaN           4           22          14  ...   
758           3               NaN           9           19          16  ...   
759          10                 1          10           16          13  ...   

    att_sv_high_right att_sv_low_right att_sv_high_left att_miss_high_left  \
0                 NaN              NaN              NaN                NaN   
1                 NaN              NaN              NaN                NaN   
2                 NaN              NaN              NaN                NaN   
3                   1                2              NaN                NaN   
4                 NaN                2                1                NaN   
..                ...              ...              ...                ...   
755               NaN                3              NaN                  1   
756               NaN              NaN                1                NaN   
757               NaN              NaN              NaN                NaN   
758               NaN              NaN              NaN                NaN   
759                 1                2              NaN                NaN   

    att_goal_high_right att_goal_high_left att_post_right  \
0                   NaN                NaN            NaN   
1                   NaN                NaN            NaN   
2                   NaN                NaN            NaN   
3                   NaN                NaN            NaN   
4                   NaN                NaN            NaN   
..                  ...                ...            ...   
755                 NaN                NaN            NaN   
756                 NaN                NaN            NaN   
757                 NaN                NaN            NaN   
758                 NaN                NaN            NaN   
759                 NaN                NaN            NaN   

    att_goal_high_centre penalty_save att_post_high  
0                    NaN          NaN           NaN  
1                    NaN          NaN           NaN  
2                    NaN          NaN           NaN  
3                    NaN          NaN           NaN  
4                    NaN          NaN           NaN  
..                   ...          ...           ...  
755                  NaN          NaN           NaN  
756                  NaN          NaN           NaN  
757                  N

In [ ]:
#mainly testing to make sure team_table stuff is converted to csv
